In [ ]:
!pip install fastdownload
from fastdownload import FastDownload
d = FastDownload()
path = d.get('https://www2.ips.biba.uni-bremen.de/~jat/fad/dataset.zip')

In [ ]:
# New Tasks
"""
1) + graph of train loss and validation loss for k=3, k=5, k=10
   + graph for loss over epochs
   all similar to what is in coopick tutorial.

3) Sequential.
    https://pytorch.org/tutorials/beginner/basics/buildmodel_tutorial.html
    https://pytorch.org/tutorials/beginner/blitz/neural_networks_tutorial.html
    
    
1) divide the dataset to smaller segments, k-folds.

    https://medium.com/dataseries/k-fold-cross-validation-with-pytorch-and-sklearn-d094aa00105f
    https://scikit-learn.org/stable/modules/generated/sklearn.model_selection.KFold.html
    https://scikit-learn.org/stable/modules/cross_validation.html
    google: kfold sklearn tutorial
    https://github.com/eugeniaring/Medium-Articles/blob/main/Pytorch/cnn_optuna.ipynb

3) (8th or 11th of August) create a larger dataset. drilling bits? the metal tip is to be installed to the drill.

      -Try to cover each angle and each orientation systematically(wodden >> metal sheets)
      - second label (0 not drilling, 1 drilling), collected with a button, the button is connected with raspberry pi. retrive the value the same way you do 
      with the angles.

4) classification of the drill machine.

    how to create a dataset for classification?

    # get number of input features for the classifier
    in_features = model.roi_heads.box_predictor.cls_score.in_features
    https://www.kaggle.com/code/pestipeti/pytorch-starter-fasterrcnn-train

    https://www.pluralsight.com/guides/image-classification-with-pytorch

    transfer learning
    https://www.pluralsight.com/guides/introduction-to-resnet

    Detection (Not a task):
    https://blog.paperspace.com/data-augmentation-for-object-detection-building-input-pipelines/

5) propose comparison b/w architectures for pose estimation.
    
  Read: https://github.com/christianversloot/machine-learning-articles/blob/main/how-to-create-a-neural-network-for-regression-with-pytorch.md
"""
# DONE:

"""
2) Augmentation. (offline (pytorch, then albumentation), then online)
    
    keypoint augmentation: https://albumentations.ai/docs/getting_started/keypoints_augmentation/
    
    https://pytorch.org/vision/stable/transforms.html
    https://colab.research.google.com/drive/109vu3F1LTzD1gdVV6cho9fKGx7lzbFll#scrollTo=u6o2H9qAjkZg
    https://albumentations.ai/docs/getting_started/image_augmentation/   # step 4 is important.
    https://albumentations.ai/docs/examples/pytorch_classification/

    https://discuss.pytorch.org/t/data-augmentation-after-creating-dataset/120835/4
    https://github.com/hyunjoonbok/bengaliai-cv19/blob/main/notebook/05_image_augmentation_1_albumentation.ipynb
    https://towardsdatascience.com/getting-started-with-albumentation-winning-deep-learning-image-augmentation-technique-in-pytorch-47aaba0ee3f8

6) rgb > gray scale, from 9 channels to 3 channels, to mimic one image input for a resnet.

7) extra task: remove dependence on opencv when resizing the images in the dataset class, if it is still exists.

2) from extra tasks
   + 3:2 vs 1:1 res angles?
   + resize by cropping to 1:1 aspect ratio
   solved by padding
"""
# OLD Tasks:
"""
0) what are the outputs for model()? How are you planning to use these outputs?

1) define the loss in the network class.
--

1.0) track the size of the input and output: use print(nn.Linear.shape) as an example

1) why does the output has this size?

2) write a training and an evaluation loop. This might be helpful: https://www.kaggle.com/code/khoongweihao/resnet-34-pytorch-starter-kit/notebook

3) choose/define the suitable loss function and optimizer.

4) check if the pipeline is error-free, then submit to Nicolas.

5.0) ssd are widely-used in pose estimation.

5) change network to posecnn or convposecnn or what Geifer et. al used in '* single prespective camera.'

"""

In [ ]:
!pip install torchsummary
from torchsummary import summary

In [ ]:
!pip install albumentations==0.4.6;

In [ ]:
#!pip install --upgrade opencv-contrib-python;

In [ ]:
img_files = path.ls(file_exts='.png').sorted()
print(img_files[0])

# 4 different frames from the same camera

In [ ]:
from PIL import Image
import cv2
import matplotlib.pyplot as plt
%matplotlib inline
# Inspect the dataset
fig = plt.figure(figsize=(10,10))
im = cv2.imread(str(img_files[0]))

print('Original image shape (h, w, c) is: ', im.shape)
for i in range(1,5):
    plt.subplot(2, 2, i)
    im = cv2.imread(str(img_files[i*3]))
    im = cv2.cvtColor(im, cv2.COLOR_BGR2RGB)
    plt.imshow(im)
    plt.title(img_files[i*3].name)
plt.show()

# Same frame from 3 cameras

In [ ]:
from PIL import Image
import cv2
import matplotlib.pyplot as plt
%matplotlib inline
# Inspect the dataset
fig = plt.figure(figsize=(10,10))
im = cv2.imread(str(img_files[0]))

print('Original image shape (h, w, c) is: ', im.shape)
for i in range(0,3):
    plt.subplot(3, 1, i+1)
    j = int(i*len(img_files)/3)
    img_idx = img_files[j]
    im =cv2.imread(str(img_idx))
    im = cv2.cvtColor(im, cv2.COLOR_BGR2RGB)
    plt.imshow(im)
    plt.title(img_idx.name)
plt.show()

In [ ]:
import re
def simple_get_z(file_name):
    '''return only Z as float from the file_name'''
    z_reg = re.compile(r'Z_(-?\d+).png$')
    return float(z_reg.search(str(file_name)).group(1))

simple_get_z(img_files[3]),img_files[3]

In [ ]:
# creation of dataset class
import os
import numpy as np
import torch
from torch.utils.data import Dataset
from torchvision.io import read_image
from torchvision import transforms
import PIL
import albumentations as A
from albumentations.pytorch.transforms import ToTensorV2


class DrillImages(Dataset):
    def __init__(self, img_dir, transform=None, target_transform=None, train_transform = None):
        regexp = re.compile(r'frame_(\d+)_')
        self.frames = list(set([int(regexp.search(str(item)).group(1)) for item in os.listdir(img_dir)]))
        self.file_names = os.listdir(img_dir)
        self.img_dir = img_dir
        self.transform = transform
        self.target_transform = target_transform
        self.train_transform = train_transform

    def __len__(self):
        return len(self.frames) # number of distinct frames

    def __getitem__(self, idx):
        frame_number = self.frames[idx]
        file_names = [item for item in self.file_names if 'frame_'+str(frame_number)+'_' in(item)]
  
        for i,f in enumerate(file_names):
        # read image file
        img_path = os.path.join(self.img_dir, f)  
        image = cv2.imread(img_path)

        # border_mode: 4 By default
        # border_mode: 0: BORDER_CONSTANT, 1: BORDER_REPLICATE, 2 : BORDER_REFLECT, 3: BORDER_WRAP , 4: BORDER_REFLECT_101

        transform = A.Compose([
        A.PadIfNeeded(min_height=640, min_width=640, border_mode=1, value=[0, 0, 0], p=1),
        A.RandomBrightnessContrast(p=0.1),
        A.HorizontalFlip(p=0.1),
        A.MotionBlur(p=0.1),
        A.OpticalDistortion(p=0.1),
        A.GaussNoise(p=0.1),
        A.GridDropout(p=0.1),
        A.GaussNoise(var_limit=350.0, p=1.0),
        ])

        image = transform(image=image)["image"]

        # convert image to grayscle
        image = cv2.cvtColor(image, cv2.COLOR_BGR2GRAY) # >>print(type(drill_dataset[0][0]))  > torch.Size([3, 640, 640]) instead of torch.Size([9, 640, 640])


        convert_tensor = transforms.ToTensor()
        #convert_tensor = ToTensorV2()    # with Albumentations library

        t = convert_tensor(image)
        if i == 0:
        t1 = t
        else:
        t1 = torch.cat([t1, t], dim=0)

        z_reg = re.compile(r'Z_(-?\d+).png$')
        angle = float(z_reg.search(str(file_names[0])).group(1))
        
        if self.transform is not None:
            image = self.transform(image = image)['image']
        if self.target_transform is not None:
            angle = self.target_transform(angle)
        return t1,angle  

In [ ]:
train_transform = A.Compose([
    A.HorizontalFlip(p=0.5),
    A.OneOf([A.MotionBlur(p=1),
             #A.OpticalDistortion(p=1),
             A.GaussNoise(p=1),
             A.GridDropout(p=1.0),
             A.GaussNoise(var_limit=350.0, p=1.0)
             ], p=1),
    ])
# you should normalize: look up the resnet documentation: see 13:50 https://www.youtube.com/watch?v=iFADsRDJhDM

In [ ]:
"""
add batch dimension first
img_batch = torch.unsqueeze(img, 0)
img_batch.shape
"""

In [ ]:
# create our dataset instance:
drill_dataset = DrillImages(path, train_transform = train_transform)

In [ ]:
len(drill_dataset)

In [ ]:
# Validate dataset tuple
print(type(drill_dataset[0]))
print(type(drill_dataset[0][0]))
print(type(drill_dataset[0][1]))

print(drill_dataset[0][0].shape)
#print(torch.permute(drill_dataset[0][0], (2, 0, 1)).size())
print(drill_dataset[0][1])

In [ ]:
drill_dataset[0][0].shape  # with gray frames : torch.Size([3, 640, 640]) 

In [ ]:
tensor_image = drill_dataset[0][0]  # drill_dataset[0][0][0:3]
#tensor_image.permute(2, 1, 0)
#plt.imshow(tensor_image)      # tensor_image.permute(1, 2, 0)
plt.imshow(tensor_image.numpy()[0], cmap='gray')

In [ ]:
import torchvision.transforms as T
tensor_image = drill_dataset[0][0][0:3]    # drill_dataset[0][0][0:3]

T.ToPILImage()(tensor_image)
plt.imshow(T.ToPILImage()(tensor_image))

In [ ]:
tensor_image = drill_dataset[0][0][0:3]    # drill_dataset[0][0][0:3]

arr = np.ndarray(tensor_image)
arr_ = np.squeeze(arr) 

plt.imshow(arr_)

In [ ]:
%matplotlib inline
# Inspect the dataset
fig = plt.figure(figsize=(10,20))
print('Original image shape (h, w, c) is: ', tensor_image.shape)
for i in range(1,9):
    plt.subplot(4, 2, i)
    tensor_image = drill_dataset[i*5][0]    # drill_dataset[i*5][0][0:3]
    plt.imshow(tensor_image)      # tensor_image.permute(1, 2, 0)
    plt.title(img_files[i*3].name)
plt.show()

In [ ]:
print(type(drill_dataset[0][0][0][0][0].item()))

In [ ]:
print(type(drill_dataset[0][1]))

## Model Creation

You can use timm if you realy want

pytorch has that also build in

In [ ]:
from torch import nn 
from torchvision.models import resnet34
res_torch = resnet34()
res_torch;

so both models are nearly the same, but both cant handle our tensors yet

In [ ]:
# Pytorch nn.Conv2d layer expects inputs of (batch_size, channels, height, width)

random_input = torch.rand([1,3,224, 224])

random_input.shape,res_torch(random_input).shape # second returns output shape of resnet34

But our tensors are not shaped that way:

In [ ]:
drill_dataset[0][0].shape

the loaded models both work on batches, so we convert our data accordingly to a batch of size 1

In [ ]:
example_data = drill_dataset[0][0]
print(example_data.shape)

example_data= drill_dataset[0][0].unsqueeze(0)
print(example_data.shape)

we need a layer that converts to the resnet input size:

In [ ]:
# torch.nn.Conv2d(in_channels, out_channels, kernel_size, stride=1, padding=0, dilation=1, groups=1, bias=True, padding_mode='zeros')
# in my case I have in_channels = 9

preprocessing_layer = nn.Conv2d(9, 3, stride = 1, kernel_size=3) # O = [(W−K+2P)/S]+1, padding = 0 , I = 224, O = ((224-3+2*0)/2) +1 = 222
print(preprocessing_layer(example_data).shape)

#print(preprocessing_layer.weight.shape);
#print(preprocessing_layer.weight);

using it with the resnet:

In [ ]:
res_torch(preprocessing_layer(example_data)).shape

finaly we need the layer to convert to a single value

In [ ]:
final_layer = nn.Linear(1000,1)
shape = final_layer(res_torch(preprocessing_layer(example_data))).shape

print('final layer output shape', shape)
print(final_layer(res_torch(preprocessing_layer(example_data))))

In [ ]:
final_layer(res_torch(preprocessing_layer(example_data)))

# Configurations

In [ ]:
DEVICE = 'cuda'

BATCH_SIZE = 1    # When batch size is changed to 2, and error occurs. "PyTorch autograd -- grad can be implicitly created only for scalar outputs"
IMG_SIZE = 224

LR = 0.001
EPOCHS = 10

# Model Class (nn.Nodule) Implementation

In [ ]:
from torch import nn 
from torchvision.models import resnet34
res_torch = resnet34()
res_torch;

In [ ]:
class MyModel(nn.Module):
    def __init__(self):
        super(MyModel, self).__init__()
        self.conv = nn.Conv2d(9, 3, stride = 1, kernel_size=3) # O = [(W−K+2P)/S]+1, padding = 0 , I = 224, O = ((224-3+2*0)/2) +1 = 222
        self.res_torch = resnet34()
        self.final = nn.Linear(1000,1)   

    def forward(self, x, angles = None): # why do I need angles=None here? bug1 # try nn.seq to 
        x = self.conv(x)
        print('Output shape of the first convolution:   ', x.shape)
        x = self.res_torch(x)
        print('Output shape of the resnet:              ', x.shape)
        #x = self.final(x) # this executed two times
        #print('Output shape of the final linear layer:  ', x.shape, '\n')
        return self.final(x)

model = MyModel()

# Remove comments to migrate the model and dataset to the GPU:

In [ ]:
model.to(DEVICE);
#example_data.to(DEVICE);

In [ ]:
#model(example_data)

#output = model(example_data)

# Shouldn't the output of the first conv layer be of shape [1, 3, 224, 224]? I think this is the input the resent34 would accpet? how is it working with 222,222?

# Here is the model summary: 

In [ ]:
summary(model, (9, 224, 224));

# Augmentation with torchvision:

In [ ]:
import torchvision.transforms as T
from pathlib import Path
from PIL import Image

In [ ]:
from PIL import Image
import matplotlib.pyplot as plt
%matplotlib inline

In [ ]:
orig_img = Image.open(Path('/root/.fastdownload/data/dataset/cam_1_frame_10_Z_31.png'))

In [ ]:
# tranform.Compose
transforms = torchvision.transforms.Compose([
    torchvision.transforms.Resize((224,224)),
    torchvision.transforms.ColorJitter(hue=.05, saturation=.05),
    torchvision.transforms.RandomHorizontalFlip(),
    torchvision.transforms.RandomRotation(20, resample=PIL.Image.BILINEAR)
])

In [ ]:
# if you want to define your own dataset class, you just have to call transforms(samples) to perform the transforms on your samples. 
transforms(drill_dataset) # ???

In [ ]:
# https://towardsdatascience.com/getting-started-with-albumentation-winning-deep-learning-image-augmentation-technique-in-pytorch-47aaba0ee3f8
# example:
torchvision_transform = transforms.Compose([
    transforms.Resize((256, 256)), 
    transforms.RandomCrop(224),
    transforms.RandomHorizontalFlip(),
    transforms.ToTensor(),
])
"""
torchvision_dataset = TorchvisionDataset(
    file_paths=["/content/drive/MyDrive/img5.jpg"],
    labels=[1],
    transform=torchvision_transform,
)
"""
# create our dataset instance:
drill_dataset = DrillImages(path,
                            transform=torchvision_transform)

# Online Augmentation with Albumentation:

In [ ]:
!pip install -U albumentations

In [ ]:
import albumentations as A
import cv2

In [ ]:
# Transofrmation with Albumentation Library
albumentations_transform_oneof = albumentations.Compose([
    albumentations.CenterCrop(480, 480, p=1.0)
    albumentations.OneOf([
                          albumentations.VerticalFlip(p=1)            
    ], p=0.5),
    albumentations.OneOf([
                          albumentations.MotionBlur(p=1),
                          albumentations.OpticalDistortion(p=1),
                          albumentations.GaussNoise(p=1)                 
    ], p=1),
    albumentations.pytorch.ToTensor()
])

# create our dataset instance:
drill_dataset = DrillImages(path,
                            transform=albumentations_transform_oneof)


albumentations_dataset = AlbumentationsDataset(
    file_paths=["/content/gdrive/My Drive/img5.png"],
    labels=[1],
    transform=albumentations_transform_oneof,
)



In [ ]:
# Transofrmation with Albumentation Library
transform = A.Compose([
    A.VerticalFlip(p=0.5),
    A.RandomBrightnessContrast(p=0.2),
    A.Normalize(mean=(0.485, 0.456, 0.406), std=(0.229, 0.224, 0.225)),
        torchvision.transforms.ColorJitter(hue=.05, saturation=.05),
])

In [ ]:
# Keypoints augmentation in Pose estimation tasks.
transform = A.Compose([
    A.RandomCrop(width=330, height=330),
    A.RandomBrightnessContrast(p=0.2),
], keypoint_params=A.KeypointParams(format='xy'))

In [ ]:
# Bounding Box augmentation
transform = A.Compose([
    A.RandomCrop(width=450, height=450),
    A.HorizontalFlip(p=0.5),
    A.RandomBrightnessContrast(p=0.2),
], bbox_params=A.BboxParams(format='coco'))

# Create dataloaders:

In [ ]:
from tqdm.notebook import tqdm    # progress bar

from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelEncoder

In [ ]:
train_ds, valid_ds = train_test_split(drill_dataset, test_size = 0.2, random_state=42) # remove randam state in production to get a truely random split.

In [ ]:
BATCH_SIZE = 1

trainloader = torch.utils.data.DataLoader(train_ds, batch_size = BATCH_SIZE, shuffle = True)
validloader = torch.utils.data.DataLoader(valid_ds, batch_size = BATCH_SIZE, shuffle = False)

In [ ]:
print("Total no. batches in trainloader : {}".format(len(trainloader)))
print("Total no. batches in validloader : {}".format(len(validloader)))

for tensor, angle in trainloader:
    break;
print("Shape of one tensor batch : {}".format(tensor.shape))
print("Shape of one angle batch  : {}".format(angle.shape))

#Train and Evaluation Functions (+ MSE Loss Function):

In [ ]:
def train_fn(model, dataloader, optimizer, loss_fn = nn.MSELoss()):
    total_loss = 0.0
    model.train() # Sets mode, dropout layers are activated. Does not call the forward function.

    for data in tqdm(dataloader):
        # bug2
        t, angles = data
        t, angles = t.to(DEVICE), angles.to(DEVICE)

        # _ ,loss = model(t, angles)
        output = model(t)
        loss = loss_fn(output.float(), angles.float()) # solves the got double but expected float error.

        optimizer.zero_grad()
        loss.backward()
        optimizer.step()


        total_loss += loss.item()

        return total_loss / len(dataloader)

In [ ]:
def eval_fn(model, dataloader, loss_fn = nn.MSELoss()):
    total_loss = 0.0
    model.eval() # Dropout OFF

    with torch.no_grad():
        for data in tqdm(dataloader):

            t, angles = data
            t, angles = t.to(DEVICE), angles.to(DEVICE)

            output = model(t)
            loss = loss_fn(output, angles)

            total_loss += loss.item()
      
            return total_loss / len(dataloader)


# Optimizer

In [ ]:
optimizer = torch.optim.Adam(model.parameters(), lr=4e-4) # have you moved the model to the gpu? if no, the model won't be optimized

In [ ]:
import numpy as np
import sys
#sys.path.append('/content/')

In [ ]:
train_loss = train_fn(model, trainloader, optimizer)

#K-folds Division:

In [ ]:
from sklearn.model_selection import KFold
from torch.utils.data import Dataset, DataLoader,TensorDataset,random_split,SubsetRandomSampler, ConcatDataset
import random

In [ ]:
k=5
splits=KFold(n_splits=k,shuffle=True,random_state=42) # delete random state in production to get truely random splits.
foldperf={}

In [ ]:
# create our dataset instance:
drill_dataset = DrillImages(path)

# Training Loop for K-folds

In [ ]:
EPOCHS = 40 

In [ ]:
for fold, (train_idx,val_idx) in enumerate(splits.split(np.arange(len(drill_dataset)))):

    print('Fold {}'.format(fold + 1))
    print('\n')
    train_sampler = SubsetRandomSampler(train_idx)
    valid_sampler = SubsetRandomSampler(val_idx)
    train_loader = DataLoader(drill_dataset, batch_size=BATCH_SIZE, sampler=train_sampler)
    valid_loader = DataLoader(drill_dataset, batch_size=BATCH_SIZE, sampler=valid_sampler)

    #device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")

    #model = ConvNet()
    #model.to(device)
    #optimizer = optim.Adam(model.parameters(), lr=0.002)

    #history = {'train_loss': [], 'valid_loss': [],'train_acc':[],'valid_acc':[]}
    history = {'train_loss': [], 'valid_loss': []}

    best_valid_loss = np.Inf
    for i in range(EPOCHS):
        train_loss = train_fn(model, trainloader, optimizer)
        valid_loss = eval_fn(model, validloader)
        print(type(valid_loss))

        if valid_loss < best_valid_loss:
        torch.save(model.state_dict(), 'best_model.pt')
        print("Weights are saved")
        best_valid_loss = valid_loss

        print(f"Epoch : {i + 1} train loss : {train_loss}, valid loss : {valid_loss}")

        history['train_loss'].append(train_loss)
        history['valid_loss'].append(valid_loss)
        #history['train_acc'].append(train_acc)
        #history['valid_acc'].append(valid_acc)

        foldperf['fold{}'.format(fold+1)] = history  

torch.save(model,'k_cross_CNN.pt')


In [ ]:
"""
epochs = 1

k = 10
Epoch : 1 train loss : 1.8225659909455671, valid loss : 38.605479277642495

k=5
Epoch : 1 train loss : 3.512660482655401, valid loss : 75.53810928017386

======

epochs = 10

k=10, considerably longer time.
Epoch : 10 train loss : 0.3141076875769574, valid loss : 109.34485905648519

k= 5
Epoch : 10 train loss : 9.08382448942765, valid loss : 46.310213895635876

====

epochs = 20

k= 5
Epoch : 20 train loss : 11.668628195057744, valid loss : 30.13095895382503

====

epochs = 40
k=5
Epoch : 40 train loss : 0.06484512142513109, valid loss : 5.343459798998083

====

epochs = 120
k=5


"""



#Training Loop

In [ ]:
best_valid_loss = np.Inf

for i in range(EPOCHS):
    train_loss = train_fn(model, trainloader, optimizer)
    valid_loss = eval_fn(model, validloader)
    print(type(valid_loss))

    if valid_loss < best_valid_loss:
    torch.save(model.state_dict(), 'best_model.pt')
    print("Weights are saved")
    best_valid_loss = valid_loss

    print(f"Epoch : {i + 1} train loss : {train_loss}, valid loss : {valid_loss}")


# RuntimeError: Input type (torch.cuda.FloatTensor) and weight type (torch.FloatTensor) should be the same device

# RuntimeError: grad can be implicitly created only for scalar outputs

# Inference

In [ ]:
image, angle = valid_ds[3] # (c, h, w)
print(angle)

In [ ]:
!pip install utils

In [ ]:
import utils

In [ ]:
model.load_state_dict(torch.load('best_model.pt'))
model.eval()

with torch.no_grad():

    t, angle = valid_ds[3] # (c, h, w)
    print(angle)
    t = t.unsqueeze(0).to(DEVICE) # (batch_size, c, h, w)
    t = t.to(DEVICE)
    
    angle  = model(t)
    print(angle)

In [ ]:
https://www.kaggle.com/code/ryanholbrook/the-convolutional-classifier

In [ ]:
https://pytorch.org/tutorials/beginner/basics/optimization_tutorial.html